In [1]:
import math
import pandas as pd
import geopandas as gpd
from geopy.geocoders import Nominatim            # What you'd normally run
import numpy as np

import folium 
from folium import Marker
from folium.plugins import MarkerCluster

# Geocoding

Geocoding is the process of converting the name of a place or an address to a location on a map.

In [2]:
# Load and preview Starbucks locations in California
starbucks = pd.read_csv("archive/starbucks_locations.csv")
starbucks.head()

Store Number               Store Name  \
0  10429-100710       Palmdale & Hwy 395   
1       635-352    Kanan & Thousand Oaks   
2   74510-27669  Vons-Agoura Hills #2001   
3  29839-255026    Target Anaheim T-0677   
4  23463-230284   Safeway - Alameda 3281   

                                   Address          City  Longitude  Latitude  
0             14136 US Hwy 395 Adelanto CA      Adelanto    -117.40     34.51  
1                5827 Kanan Road Agoura CA        Agoura    -118.76     34.16  
2           5671 Kanan Rd. Agoura Hills CA  Agoura Hills    -118.76     34.15  
3  8148 E SANTA ANA CANYON ROAD AHAHEIM CA       AHAHEIM    -117.75     33.87  
4               2600 5th Street Alameda CA       Alameda    -122.28     37.79

In [3]:
starbucks.isna().sum()

Store Number    0
Store Name      0
Address         0
City            0
Longitude       5
Latitude        5
dtype: int64

In [4]:
rows_with_missing = starbucks[starbucks["Longitude"].isna() | starbucks["Latitude"].isna()]
rows_with_missing

Store Number                Store Name  \
153      5406-945  2224 Shattuck - Berkeley   
154       570-512                Solano Ave   
155  17877-164526   Safeway - Berkeley #691   
156  19864-202264         Telegraph & Ashby   
157     9217-9253           2128 Oxford St.   

                               Address      City  Longitude  Latitude  
153   2224 Shattuck Avenue Berkeley CA  Berkeley        NaN       NaN  
154     1799 Solano Avenue Berkeley CA  Berkeley        NaN       NaN  
155    1444 Shattuck Place Berkeley CA  Berkeley        NaN       NaN  
156  3001 Telegraph Avenue Berkeley CA  Berkeley        NaN       NaN  
157     2128 Oxford Street Berkeley CA  Berkeley        NaN       NaN

In [5]:
# user_agent 可以是任何字符串，但要是独特的
# user_agent 是用来标识你这个应用/脚本的（防止滥用）
geolocator = Nominatim(user_agent='2025.4.22')

def geocoder(address):
    point = geolocator.geocode(address).point
    return pd.Series({
        'Longitude':point.longitude, 'Latitude':point.latitude
    })

berkeley_locations = rows_with_missing['Address'].apply(geocoder)
starbucks.update(berkeley_locations)

In [6]:
starbucks[starbucks['City']=='Berkeley']

Store Number                Store Name  \
153      5406-945  2224 Shattuck - Berkeley   
154       570-512                Solano Ave   
155  17877-164526   Safeway - Berkeley #691   
156  19864-202264         Telegraph & Ashby   
157     9217-9253           2128 Oxford St.   

                               Address      City   Longitude   Latitude  
153   2224 Shattuck Avenue Berkeley CA  Berkeley -122.268230  37.868839  
154     1799 Solano Avenue Berkeley CA  Berkeley -122.280013  37.891477  
155    1444 Shattuck Place Berkeley CA  Berkeley -122.269679  37.880907  
156  3001 Telegraph Avenue Berkeley CA  Berkeley -122.259406  37.855903  
157     2128 Oxford Street Berkeley CA  Berkeley -122.266095  37.870253

In [7]:
berkeley_locations

Longitude   Latitude
153 -122.268230  37.868839
154 -122.280013  37.891477
155 -122.269679  37.880907
156 -122.259406  37.855903
157 -122.266095  37.870253

In [8]:
m_1 = folium.Map(location=[37.88,-122.26], zoom_start=13)

for idx, row in starbucks.iterrows():
    try:
        Marker(
            # 注意坐标顺序，（纬度，经度）
            location=[row['Latitude'],row['Longitude']],
            popup=row['Store Name']
        ).add_to(m_1)
    except:
        pass

m_1

# Table joins

<font size=5>Spatial join</font>

With a spatial join, we combine GeoDataFrames based on the spatial relationship between the objects in the "geometry" columns.

```bash
gpd.sjoin() 是 GeoPandas 中用来做 空间连接（spatial join）的一个函数，它的作用是：

根据地理位置，把两个 GeoDataFrame 拼起来，就像 pd.merge() 是按列拼，gpd.sjoin() 是按空间关系进行拼接

```python
gpd.sjoin(left_df, right_df, how="inner", predicate="intersects")


参数名 | 说明
|------|------|
left_df | 左边的 GeoDataFrame（比如点数据）
right_df | 右边的 GeoDataFrame（比如多边形数据）
how | 连接方式（类似 pandas 的 merge）： - 'inner'：只保留匹配上的行 - 'left'：保留左边所有数据，加上匹配上的右边信息
predicate | 空间关系，用来判断两个对象是否“匹配”常见有： - 'intersects'：是否相交（默认） - 'within'：左边是否在右边内部 - 'contains'：右边是否包含左边 - 'touches'：边界是否接触 - 'crosses'：是否穿过
lsuffix, rsuffix | 避免两边有重复列名冲突（可选）

In [9]:
starbucks_geo = gpd.GeoDataFrame(data=starbucks, geometry=gpd.points_from_xy(x=starbucks.Longitude, y=starbucks.Latitude))
starbucks_geo = starbucks_geo.set_crs('epsg:4326')  # 记得赋值
starbucks_geo.crs is None

False

In [10]:
CA_counties = gpd.read_file("archive/CA_county_boundaries/CA_county_boundaries/CA_county_boundaries.shp")
CA_counties = CA_counties.set_crs('epsg:4326')

# 使用 sjoin() 前，两个 GeoDataFrame 的坐标系（CRS）必须一致
CA_pop = pd.read_csv("archive/CA_county_population.csv", index_col="GEOID")
CA_high_earners = pd.read_csv("archive/CA_county_high_earners.csv", index_col="GEOID")
CA_median_age = pd.read_csv("archive/CA_county_median_age.csv", index_col="GEOID")

cols_to_add = CA_pop.join([CA_high_earners, CA_median_age]).reset_index()
CA_stats = CA_counties.merge(cols_to_add, on="GEOID")
CA_stats["density"] = CA_stats["population"] / CA_stats["area_sqkm"]
CA_stats.head()

GEOID                  name    area_sqkm  \
0   6091         Sierra County  2491.995494   
1   6067     Sacramento County  2575.258262   
2   6083  Santa Barbara County  9813.817958   
3   6009      Calaveras County  2685.626726   
4   6111        Ventura County  5719.321379   

                                            geometry  population  \
0  POLYGON ((-120.6556 39.69357, -120.65554 39.69...        2987   
1  POLYGON ((-121.18858 38.71431, -121.18732 38.7...     1540975   
2  MULTIPOLYGON (((-120.58191 34.09856, -120.5822...      446527   
3  POLYGON ((-120.63095 38.34111, -120.63058 38.3...       45602   
4  MULTIPOLYGON (((-119.63631 33.27304, -119.6360...      850967   

   high_earners  median_age     density  
0           111        55.0    1.198638  
1         65768        35.9  598.376878  
2         25231        33.7   45.499825  
3          2046        51.6   16.980022  
4         57121        37.5  148.788107

In [11]:
sel_feature = (CA_stats.high_earners > 100000) &\
                         (CA_stats.median_age < 38.5) &\
                         (CA_stats.density > 285) &\
                         ((CA_stats.median_age < 35.5) |\
                         (CA_stats.density > 1400) |\
                         (CA_stats.high_earners > 500000))
sel_counties = CA_stats[sel_feature]

In [12]:
# 空间连接
locations_interested = gpd.sjoin(
    left_df=starbucks_geo,
    right_df=sel_counties,
    how='inner',
    predicate='intersects'
)
locations_interested.head()

Store Number                   Store Name  \
1        635-352        Kanan & Thousand Oaks   
2    74510-27669      Vons-Agoura Hills #2001   
14   76365-97162        Target Alhambra T-184   
15    6794-41839     Fremont Ave & Mission Rd   
16  11220-104633  Atlantic & Valley, Alhambra   

                                  Address          City  Longitude  Latitude  \
1               5827 Kanan Road Agoura CA        Agoura    -118.76     34.16   
2          5671 Kanan Rd. Agoura Hills CA  Agoura Hills    -118.76     34.15   
14      1220 West Main Street Alhambra CA      Alhambra    -118.14     34.09   
15      1131 S Fremont Ave, A Alhambra CA      Alhambra    -118.15     34.08   
16  1410 South Atlantic Blvd. Alhambra CA      Alhambra    -118.13     34.08   

                 geometry  index_right  GEOID                name  \
1   POINT (-118.76 34.16)            5   6037  Los Angeles County   
2   POINT (-118.76 34.15)            5   6037  Los Angeles County   
14  POINT (-118.14 34.09)            5   6037  Los Angeles County   
15  POINT (-118.15 34.08)            5   6037  Los Angeles County   
16  POINT (-118.13 34.08)            5   6037  Los Angeles County   

       area_sqkm  population  high_earners  median_age     density  
1   12305.376879    10105518        501413        36.0  821.227834  
2   12305.376879    10105518        501413        36.0  821.227834  
14  12305.376879    10105518        501413        36.0  821.227834  
15  12305.376879    10105518        501413        36.0  821.227834  
16  12305.376879    10105518        501413        36.0  821.227834

In [13]:
locations_interested.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 1043 entries, 1 to 2808
Data columns (total 15 columns):
 #   Column        Non-Null Count  Dtype   
---  ------        --------------  -----   
 0   Store Number  1043 non-null   object  
 1   Store Name    1043 non-null   object  
 2   Address       1043 non-null   object  
 3   City          1043 non-null   object  
 4   Longitude     1043 non-null   float64 
 5   Latitude      1043 non-null   float64 
 6   geometry      1043 non-null   geometry
 7   index_right   1043 non-null   int64   
 8   GEOID         1043 non-null   int64   
 9   name          1043 non-null   object  
 10  area_sqkm     1043 non-null   float64 
 11  population    1043 non-null   int64   
 12  high_earners  1043 non-null   int64   
 13  median_age    1043 non-null   float64 
 14  density       1043 non-null   float64 
dtypes: float64(5), geometry(1), int64(4), object(5)
memory usage: 130.4+ KB


In [14]:
m_2 = folium.Map(location=[37,-120], zoom_start=6)

mc = MarkerCluster()
for idx,row in locations_interested.iterrows():
    try:
        Marker(
            location=[row['Latitude'],row['Longitude']],
            popup=row['Store Name']
        ).add_to(mc)
    except:
        pass
mc.add_to(m_2)

m_2